In [1]:
import re
from pymongo import MongoClient
import pandas as pd
import nltk
from nltk.probability import FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
import string

In [2]:
# Koneksi ke MongoDB
client = MongoClient('mongodb://localhost:27017/')
db = client['google_play_store_data']
collection = db['prepocessing_data_bibit']

In [3]:
# Menghapus field yang tidak diperlukan
collection.update_many({}, {'$unset': {'reviewId': '', 'userName': '', 'userImage': '', 'score': '',
                                       'thumbsUpCount': '', 'reviewCreatedVersion': '','at': '','replyContent': '',
                                       'repliedAt': '', 'appVersion': ''}})

# Menampilkan data setelah penghapusan field
cursor = collection.find()
for document in cursor:
    print(document)

{'_id': ObjectId('6638614cdd520c9ba22ee66c'), 'content': 'Mau daftar aj di persulit dari bulan April gagal melulu. Daftar pertama foto diri sama KTP ,status gagal. Perbaikan foto diri sama SIM A, kembali lagi gagal. Perbaikan kembali foto diri sama SIM A + KTP, kembali lagi gagal. Chat admin idak membantu jadi males.'}
{'_id': ObjectId('6638614cdd520c9ba22ee66d'), 'content': 'Aku ngerasa ini apps kyknya palsu deh, kyk binomo bukan naik malah turun drastis banget kalo lewat dari 500rb ke atas saldo saya kalau 100rb gk pernah tuh ada yang namanya turun uangnya mau pakai bibit kyknya gk lagi² deh bukanya untung malah buntung'}
{'_id': ObjectId('6638614cdd520c9ba22ee66e'), 'content': 'MAAF SEBELUMNYA SAYA KASIH TAU JANGAN INVEST TERLALU BANYAK DI BIBIT KETIKA PENCAIRAN SALDO GAK MASUK SAYA UDAH HAMPIR 2 MINGGU GA MASUK² PADAHAL LAGI BUTUH BANGT BUAT RUMAH SAKIT TAPI CUMA MASUK 13K DOANG KECEWAA BERAT, UDAH GITU MASA SALDO REKENING TIBA² DI POTONG SNDIRI PADAHAL GA BELI APA² TIBA² MOTONG SN

In [4]:
# Mengambil data dari koleksi "review"
reviews = collection.find()

# Menghitung total jumlah huruf yang diubah menjadi huruf kecil
total_lowercase_chars = 0
for review in reviews:
    original_review = review['content']
    lowercase_review = original_review.lower()
    
    # Menghitung jumlah huruf yang berubah menjadi huruf kecil
    for i in range(len(original_review)):
        if original_review[i] != lowercase_review[i]:
            total_lowercase_chars += 1

    # Update data pada koleksi "review" dengan teks yang sudah diubah menjadi huruf kecil
    collection.update_one(
        {'_id': review['_id']},
        {'$set': {'content': lowercase_review}},

    )

# Menampilkan total jumlah huruf yang diubah menjadi huruf kecil
print(f"Total jumlah huruf yang diubah menjadi huruf kecil: {total_lowercase_chars}")

Total jumlah huruf yang diubah menjadi huruf kecil: 28980


In [5]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def remove_ascii(text):
    modified_text = text.encode('ascii', 'replace').decode('ascii')
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
cursor = collection.find()

total_cleaned_count = 0

for document in cursor:
    review = document['content']
    cleaned_review, cleaned_count = remove_ascii(review)

    # Memperbarui dokumen dengan review yang sudah bersih
    collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah karakter non-ascii yang dihapus
print(f"Jumlah karakter non-ASCII yang dihapus: {total_cleaned_count}")


Jumlah karakter non-ASCII yang dihapus: 1841


In [6]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def remove_punctuation(text):
    """Menghapus tanda baca dari teks."""
    # Pola regex untuk tanda baca
    punctuation_pattern = r'[' + re.escape(string.punctuation) + ']'
    
    # Menghapus tanda baca menggunakan regex
    modified_text = re.sub(punctuation_pattern, '', text)
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_punctuation(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah tanda baca yang dihapus
print(f"Jumlah tanda baca yang dihapus: {total_cleaned_count}")


Jumlah tanda baca yang dihapus: 568078


In [7]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def remove_number(text):
    """Menghapus angka dari teks."""
    modified_text = re.sub(r"\d+", " ", text)
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_number(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah angka yang dihapus
print(f"Jumlah angka yang dihapus: {total_cleaned_count}")

Jumlah angka yang dihapus: 99047


In [8]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def remove_singl_char(text):
    """Menghapus karakter tunggal dari teks."""
    modified_text = re.sub(r"\b[a-zA-Z]\b", " ", text)
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_singl_char(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah karakter tunggal yang dihapus
print(f"Jumlah karakter tunggal yang dihapus: {total_cleaned_count}")


Jumlah karakter tunggal yang dihapus: 932


In [9]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def normalize_whitespace(text):
    """Memperbaiki spasi yang tidak teratur."""
    modified_text = re.sub(r'\s+', ' ', text).strip()
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = normalize_whitespace(review)
    
    # Memperbarui dokumen dengan review yang sudah dibenarkan
    collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah whitespace yang dihapus
print(f"Jumlah whitespace yang dihapus: {total_cleaned_count}")


Jumlah whitespace yang dihapus: 274023


In [10]:
# Load data dari file Excel
df = pd.read_excel('normalized2.xlsx')

# Membuat dictionary dari data yang dibaca
abbreviations = dict(zip(df['before'], df['after']))

def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def expand_abbreviations(text):
    tokens = text.split()
    expanded_tokens = [abbreviations.get(word.lower(), word) for word in tokens]
    expanded_text = ' '.join(expanded_tokens)
    
    changes_count = count_changes(text, expanded_text)

    return expanded_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_expanded_count = 0

for document in documents:
    review = document['content']
    expanded_review, expanded_count = expand_abbreviations(review)
    
    # Memperbarui dokumen dengan review yang sudah diekspansi
    collection.update_one({'_id': document['_id']}, {'$set': {'content': expanded_review}})

    total_expanded_count += expanded_count

# Menampilkan jumlah kata yang dinormalisasi
print(f"Jumlah kata yang dinormalisasi: {total_expanded_count}")


Jumlah kata yang dinormalisasi: 412086


In [11]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def remove_duplicate_chars(text):
    words = text.split()
    cleaned_words = []
    changes_count = 0
    for word in words:
        cleaned_word = re.sub(r'(\w)\1+', r'\1', word)
        changes_count += count_changes(word, cleaned_word)
        cleaned_words.append(cleaned_word)
    
    cleaned_text = " ".join(cleaned_words)

    return cleaned_text, changes_count

# Mendapatkan data dari koleksi MongoDB
cursor = collection.find()

total_changes_count = 0

for document in cursor:
    review = document['content']
    
    # Menghapus karakter ganda dalam review
    cleaned_review, changes_count = remove_duplicate_chars(review)
    
    # Memperbarui field 'review' dengan review yang sudah dibersihkan
    collection.update_one(
        {'_id': document['_id']},
        {'$set': {'content': cleaned_review}}
    )

    total_changes_count += changes_count

# Menampilkan jumlah karakter ganda yang dihapus
print(f"Jumlah karakter ganda yang dihapus: {total_changes_count}")


Jumlah karakter ganda yang dihapus: 11208


In [12]:
# Load data dari file Excel
df = pd.read_excel('normalized2.xlsx')

# Membuat dictionary dari data yang dibaca
abbreviations = dict(zip(df['before'], df['after']))

def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def expand_abbreviations(text):
    tokens = text.split()
    expanded_tokens = [abbreviations.get(word.lower(), word) for word in tokens]
    expanded_text = ' '.join(expanded_tokens)
    
    changes_count = count_changes(text, expanded_text)

    return expanded_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = collection.find()

total_expanded_count = 0

for document in documents:
    review = document['content']
    expanded_review, expanded_count = expand_abbreviations(review)
    
    # Memperbarui dokumen dengan review yang sudah diekspansi
    collection.update_one({'_id': document['_id']}, {'$set': {'content': expanded_review}})

    total_expanded_count += expanded_count

# Menampilkan jumlah kata yang dinormalisasi
print(f"Jumlah kata yang dinormalisasi: {total_expanded_count}")


Jumlah kata yang dinormalisasi: 42081


In [13]:
# Mendapatkan data dari koleksi MongoDB
cursor = collection.find()

for document in cursor:
    review = document['content']
    
    # Melakukan tokenisasi menggunakan word_tokenize dari nltk
    tokens = word_tokenize(review)
    
    # Memperbarui field 'tokenized_review' dengan daftar token
    collection.update_one(
        {'_id': document['_id']},
        {'$set': {'tokenized_review': tokens}}
    )

    print(tokens)

['mau', 'daftar', 'saja', 'di', 'persulit', 'dari', 'bulan', 'april', 'gagal', 'melulu', 'daftar', 'pertama', 'foto', 'diri', 'sama', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'diri', 'sama', 'sim', 'kembali', 'lagi', 'gagal', 'perbaikan', 'kembali', 'foto', 'diri', 'sama', 'sim', 'ktp', 'kembali', 'lagi', 'gagal', 'pertanyaan', 'admin', 'idak', 'membantu', 'jadi', 'males']
['aku', 'ngerasa', 'ini', 'aps', 'sepertinya', 'palsu', 'sudah', 'seperti', 'binomo', 'bukan', 'naik', 'malah', 'turun', 'drastis', 'sangat', 'kalo', 'lewat', 'dari', 'rb', 'ke', 'atas', 'saldo', 'saya', 'kalau', 'rb', 'tidak', 'pernah', 'itu', 'ada', 'yang', 'namanya', 'turun', 'uangnya', 'mau', 'pakai', 'bibit', 'sepertinya', 'tidak', 'lagi', 'sudah', 'bukanya', 'untung', 'malah', 'buntung']
['maf', 'sebelumnya', 'saya', 'kasih', 'tau', 'jangan', 'invest', 'terlalu', 'banyak', 'di', 'bibit', 'ketika', 'pencairan', 'saldo', 'tidak', 'masuk', 'saya', 'sudah', 'hampir', 'mingu', 'tidak', 'masuk', 'padahal', 'lag

['jaringan', 'bagus', 'dibilang', 'gada', 'koneksi', 'tidak', 'jelas', 'sekarang', 'apknya']
['kalo', 'mau', 'masuk', 'apk', 'bibit', 'loading', 'nya', 'lama', 'sekali', 'tolong', 'diperbaiki']
['padahal', 'sudah', 'melakukan', 'penjualan', 'bukanya', 'masuk', 'ke', 'walet', 'malah', 'berkurang', 'terus']
['saya', 'mau', 'investasi', 'tapi', 'registrasi', 'tidak', 'selesai', 'registrasi', 'aja', 'lama', 'bngt', 'sudah', 'selesai', 'pakai', 'gagal', 'nungu', 'lama', 'lagi', 'parah', 'menungu', 'verifikasi', 'aja', 'sampe', 'hari']
['tolong', 'untuk', 'waktu', 'pencairan', 'dipercepat', 'lagi', 'la', 'masak', 'mingu', 'belum', 'cair']
['skrup', 'sering', 'lepas', 'terus', 'lemot', 'kadang', 'gabisa', 'di', 'buka', 'aplikasi', 'nya']
['sudah', 'input', 'data', 'benar', 'malah', 'di', 'reject']
['verifikasinya', 'lama', 'sudah', 'hari', 'tidak', 'dikonfirmasimakasih']
['terlalu', 'lama', 'verifikasi', 'dari', 'bibitnya', 'sendiribikin', 'malesverifikasi', 'aja', 'susah', 'makanya', 'banyak

In [14]:
# Download data pendukung nltk (hanya perlu dilakukan sekali)
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\miase\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [15]:
# Mendapatkan data dari koleksi MongoDB
cursor = collection.find()

# Mengambil daftar stopwords dalam bahasa Indonesia
stopwords_indonesia = set(stopwords.words('indonesian'))

for document in cursor:
    review = document['tokenized_review']
    
    # Menghapus stopwords dari review menggunakan stopwords dalam bahasa Indonesia
    filtered_review = [word for word in review if word.lower() not in stopwords_indonesia]
    
    # Memperbarui field 'filtered_review' dengan review yang sudah tidak mengandung stopwords
    collection.update_one(
        {'_id': document['_id']},
        {'$set': {'filtered_review': filtered_review}}
    )

    print (filtered_review)

['daftar', 'persulit', 'april', 'gagal', 'melulu', 'daftar', 'foto', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'sim', 'gagal', 'perbaikan', 'foto', 'sim', 'ktp', 'gagal', 'admin', 'idak', 'membantu', 'males']
['ngerasa', 'aps', 'palsu', 'binomo', 'turun', 'drastis', 'kalo', 'rb', 'saldo', 'rb', 'namanya', 'turun', 'uangnya', 'pakai', 'bibit', 'bukanya', 'untung', 'buntung']
['maf', 'kasih', 'tau', 'invest', 'bibit', 'pencairan', 'saldo', 'masuk', 'mingu', 'masuk', 'bangt', 'rumah', 'sakit', 'masuk', 'aja', 'kecewa', 'berat', 'gitu', 'saldo', 'rekening', 'potong', 'sendoro', 'beli', 'motong', 'sendoro', 'bln', 'jqngan', 'ple', 'bibit', 'anjing', 'kali', 'ya', 'dana', 'potong', 'gajelas', 'download', 'apk', 'gajelas', 'motongin', 'uang', 'bln', 'aneh']
['sampah', 'jual', 'harga', 'tingi', 'verifikasi', 'penjualan', 'ngikut', 'harga', 'kesokan', 'harinya']
['pencairan', 'rb', 'aja', 'jt', 'maksimal', 'kerja', 'lawak']
['ribet', 'mengunakan', 'nya']
['verifikasi', 'akun', 'sat', 'peng

In [16]:
# Inisialisasi objek stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()

# Mendapatkan data dari koleksi MongoDB
cursor = collection.find()

for document in cursor:
    filtered_review = document['filtered_review']
    
    # Melakukan stemming pada setiap kata dalam filtered_review
    stemmed_review = [stemmer.stem(word) for word in filtered_review]
    
    # Memperbarui field 'stemmed_review' dengan hasil stemming
    collection.update_one(
        {'_id': document['_id']},
        {'$set': {'stemmed_review': stemmed_review}}
    )

    print (stemmed_review)


['daftar', 'sulit', 'april', 'gagal', 'melulu', 'daftar', 'foto', 'ktp', 'status', 'gagal', 'baik', 'foto', 'sim', 'gagal', 'baik', 'foto', 'sim', 'ktp', 'gagal', 'admin', 'idak', 'bantu', 'males']
['ngerasa', 'aps', 'palsu', 'binomo', 'turun', 'drastis', 'kalo', 'rb', 'saldo', 'rb', 'nama', 'turun', 'uang', 'pakai', 'bibit', 'buka', 'untung', 'buntung']
['maf', 'kasih', 'tau', 'invest', 'bibit', 'cair', 'saldo', 'masuk', 'mingu', 'masuk', 'bangt', 'rumah', 'sakit', 'masuk', 'aja', 'kecewa', 'berat', 'gitu', 'saldo', 'rekening', 'potong', 'ndoro', 'beli', 'motong', 'ndoro', 'bln', 'jqngan', 'ple', 'bibit', 'anjing', 'kali', 'ya', 'dana', 'potong', 'gajelas', 'download', 'apk', 'gajelas', 'motongin', 'uang', 'bln', 'aneh']
['sampah', 'jual', 'harga', 'tingi', 'verifikasi', 'jual', 'ngikut', 'harga', 'sok', 'hari']
['cair', 'rb', 'aja', 'jt', 'maksimal', 'kerja', 'lawak']
['ribet', 'mengunakan', 'nya']
['verifikasi', 'akun', 'sat', 'aju', 'hapus', 'akun', 'ikut', 'prosedur', 'template', 

In [17]:
# Mendapatkan data dari koleksi MongoDB
cursor = collection.find()

for document in cursor:
    stemmed_review = document['stemmed_review']
    
    # Mengubah array kata hasil stemming menjadi string
    data_clean = ' '.join(stemmed_review)
    
    # Memperbarui field 'data_clean' dengan hasil yang sudah diubah
    collection.update_one(
        {'_id': document['_id']},
        {'$set': {'data_clean': data_clean}}
    )

    print (data_clean)


daftar sulit april gagal melulu daftar foto ktp status gagal baik foto sim gagal baik foto sim ktp gagal admin idak bantu males
ngerasa aps palsu binomo turun drastis kalo rb saldo rb nama turun uang pakai bibit buka untung buntung
maf kasih tau invest bibit cair saldo masuk mingu masuk bangt rumah sakit masuk aja kecewa berat gitu saldo rekening potong ndoro beli motong ndoro bln jqngan ple bibit anjing kali ya dana potong gajelas download apk gajelas motongin uang bln aneh
sampah jual harga tingi verifikasi jual ngikut harga sok hari
cair rb aja jt maksimal kerja lawak
ribet mengunakan nya
verifikasi akun sat aju hapus akun ikut prosedur template teman cek yakak repeat progres
verifikasi semingu terima terima kecewa
pakai bank jago akun aja susah pakai aja
apk bagus gada catat riwayat hasil jual tau aset jual laku dana nya mutasi rekening
pemeliharan rdn walet nya bosok isi cocok cek kg nongol nongol saldo hadeh
proses beli ribet makan hal proses cair
baharu suka login habis
gimana s

In [18]:
# Mengecek dan menghapus dokumen dengan field "data_clean" yang kosong
query = {'data_clean': {'$exists': True, '$eq': ''}}
result = collection.delete_many(query)
print(f"Jumlah dokumen yang dihapus: {result.deleted_count}")

Jumlah dokumen yang dihapus: 151


In [19]:
# Pipeline untuk menghilangkan data duplikat berdasarkan field "data_clean"
pipeline = [
    {
        '$group': {
            '_id': '$data_clean',
            'uniqueIds': {'$addToSet': '$_id'},
            'count': {'$sum': 1}
        }
    },
    {
        '$match': {
            'count': {'$gt': 1}
        }
    }
]

# Eksekusi pipeline
duplicates = list(collection.aggregate(pipeline))

# Menghapus data duplikat
total_duplicates_removed = 0
for duplicate in duplicates:
    review_ids_to_remove = duplicate['uniqueIds'][1:]
    result = collection.delete_many({'_id': {'$in': review_ids_to_remove}})
    duplicates_removed_count = result.deleted_count
    total_duplicates_removed += duplicates_removed_count

print('Jumlah data duplikat yang dihapus:', total_duplicates_removed)


Jumlah data duplikat yang dihapus: 1128


In [20]:
stopwords_indonesia

{'ada',
 'adalah',
 'adanya',
 'adapun',
 'agak',
 'agaknya',
 'agar',
 'akan',
 'akankah',
 'akhir',
 'akhiri',
 'akhirnya',
 'aku',
 'akulah',
 'amat',
 'amatlah',
 'anda',
 'andalah',
 'antar',
 'antara',
 'antaranya',
 'apa',
 'apaan',
 'apabila',
 'apakah',
 'apalagi',
 'apatah',
 'artinya',
 'asal',
 'asalkan',
 'atas',
 'atau',
 'ataukah',
 'ataupun',
 'awal',
 'awalnya',
 'bagai',
 'bagaikan',
 'bagaimana',
 'bagaimanakah',
 'bagaimanapun',
 'bagi',
 'bagian',
 'bahkan',
 'bahwa',
 'bahwasanya',
 'baik',
 'bakal',
 'bakalan',
 'balik',
 'banyak',
 'bapak',
 'baru',
 'bawah',
 'beberapa',
 'begini',
 'beginian',
 'beginikah',
 'beginilah',
 'begitu',
 'begitukah',
 'begitulah',
 'begitupun',
 'bekerja',
 'belakang',
 'belakangan',
 'belum',
 'belumlah',
 'benar',
 'benarkah',
 'benarlah',
 'berada',
 'berakhir',
 'berakhirlah',
 'berakhirnya',
 'berapa',
 'berapakah',
 'berapalah',
 'berapapun',
 'berarti',
 'berawal',
 'berbagai',
 'berdatangan',
 'beri',
 'berikan',
 'berikut'

In [26]:
collection.update_many(
    {},
    {
        '$set': {
            'label': None
        }
    }
)

InvalidOperation: Cannot use MongoClient after close

In [38]:
import pandas as pd
from pymongo import MongoClient

# Menghubungkan ke server MongoDB (secara lokal)
client = MongoClient('localhost', 27017)

# Memilih database yang akan digunakan (jika tidak ada, akan dibuat)
db = client['google_play_store_data']

# Memilih koleksi dalam database (jika tidak ada, akan dibuat)
collection = db['prepocessing_data_bibit']  # Mengganti 'nama_koleksi' dengan 'product_reviews'

# Mengambil semua dokumen dalam koleksi
cursor = collection.find()

collection.update_many(
    {},
    {
        '$set': {
            'label': None
        }
    }
)
# Mengonversi data ke dalam bentuk DataFrame
df_bibit= pd.DataFrame(list(cursor))

# Menutup koneksi dengan server MongoDB

client.close()

df_bibit



_id  \
0     6638614cdd520c9ba22ee66c   
1     6638614cdd520c9ba22ee66d   
2     6638614cdd520c9ba22ee66e   
3     6638614cdd520c9ba22ee66f   
4     6638614cdd520c9ba22ee670   
...                        ...   
8447  663864e9dd520c9ba22f284a   
8448  663864e9dd520c9ba22f284b   
8449  663864e9dd520c9ba22f284c   
8450  663864e9dd520c9ba22f284d   
8451  663864e9dd520c9ba22f284e   

                                                content  \
0     mau daftar saja di persulit dari bulan april g...   
1     aku ngerasa ini aps sepertinya palsu sudah sep...   
2     maf sebelumnya saya kasih tau jangan invest te...   
3     sampah sudah jual di harga tingi tapi karena a...   
4     pencairan rb aja seperti jt maksimal hari kerj...   
...                                                 ...   
8447  aku suka ini aplikasi next adain beli emas don...   
8448  aplikasi yang banyak manfatnya terutama yang s...   
8449  salah satu aplikasi aperd yang layak dintal da...   
8450  sat daftar masukan kode referal fareltolemba a...   
8451  sumpah saya suka sangat sama ini aplikasi cuku...   

                                       tokenized_review  \
0     [mau, daftar, saja, di, persulit, dari, bulan,...   
1     [aku, ngerasa, ini, aps, sepertinya, palsu, su...   
2     [maf, sebelumnya, saya, kasih, tau, jangan, in...   
3     [sampah, sudah, jual, di, harga, tingi, tapi, ...   
4     [pencairan, rb, aja, seperti, jt, maksimal, ha...   
...                                                 ...   
8447  [aku, suka, ini, aplikasi, next, adain, beli, ...   
8448  [aplikasi, yang, banyak, manfatnya, terutama, ...   
8449  [salah, satu, aplikasi, aperd, yang, layak, di...   
8450  [sat, daftar, masukan, kode, referal, fareltol...   
8451  [sumpah, saya, suka, sangat, sama, ini, aplika...   

                                        filtered_review  \
0     [daftar, persulit, april, gagal, melulu, dafta...   
1     [ngerasa, aps, palsu, binomo, turun, drastis, ...   
2     [maf, kasih, tau, invest, bibit, pencairan, sa...   
3     [sampah, jual, harga, tingi, verifikasi, penju...   
4      [pencairan, rb, aja, jt, maksimal, kerja, lawak]   
...                                                 ...   
8447  [suka, aplikasi, next, adain, beli, emas, dola...   
8448  [aplikasi, manfatnya, khilaf, belanja, keuanga...   
8449  [salah, aplikasi, aperd, layak, dintal, berinv...   
8450  [sat, daftar, masukan, kode, referal, fareltol...   
8451  [sumpah, suka, aplikasi, bintang, berbicara, w...   

                                         stemmed_review  \
0     [daftar, sulit, april, gagal, melulu, daftar, ...   
1     [ngerasa, aps, palsu, binomo, turun, drastis, ...   
2     [maf, kasih, tau, invest, bibit, cair, saldo, ...   
3     [sampah, jual, harga, tingi, verifikasi, jual,...   
4           [cair, rb, aja, jt, maksimal, kerja, lawak]   
...                                                 ...   
8447  [suka, aplikasi, next, adain, beli, emas, dola...   
8448  [aplikasi, manfatnya, khilaf, belanja, uang, r...   
8449  [salah, aplikasi, aperd, layak, dintal, invest...   
8450  [sat, daftar, masuk, kode, referal, fareltolem...   
8451  [sumpah, suka, aplikasi, bintang, bicara, wlw,...   

                                             data_clean  label test  
0     daftar sulit april gagal melulu daftar foto kt...    0.0       
1     ngerasa aps palsu binomo turun drastis kalo rb...    NaN       
2     maf kasih tau invest bibit cair saldo masuk mi...    NaN       
3     sampah jual harga tingi verifikasi jual ngikut...    NaN       
4                   cair rb aja jt maksimal kerja lawak    NaN       
...                                                 ...    ...  ...  
8447  suka aplikasi next adain beli emas dolar index...    NaN       
8448  aplikasi manfatnya khilaf belanja uang rencana...    NaN       
8449  salah aplikasi aperd layak dintal investasi fi...    NaN       
8450  sat daftar masuk kode referal fareltolemba lan...    NaN       
8451  sumpah

In [30]:
clean_bibit_data = df_bibit[['data_clean', 'label']]
clean_bibit_data

data_clean label
0     daftar sulit april gagal melulu daftar foto kt...  None
1     ngerasa aps palsu binomo turun drastis kalo rb...  None
2     maf kasih tau invest bibit cair saldo masuk mi...  None
3     sampah jual harga tingi verifikasi jual ngikut...  None
4                   cair rb aja jt maksimal kerja lawak  None
...                                                 ...   ...
8447  suka aplikasi next adain beli emas dolar index...  None
8448  aplikasi manfatnya khilaf belanja uang rencana...  None
8449  salah aplikasi aperd layak dintal investasi fi...  None
8450  sat daftar masuk kode referal fareltolemba lan...  None
8451  sumpah suka aplikasi bintang bicara wlw kendal...  None

[8452 rows x 2 columns]

In [32]:
clean_bibit_data.to_excel('clean_bibit_data2.xlsx', index=False)

In [36]:
df_bibit.label.value_counts(dropna=False)

label
NaN    8451
0.0       1
Name: count, dtype: int64